In [25]:
import pandas as pd
import numpy as np
import scipy

In [40]:
fp = '../results/01282021_new/som_germ_cnv_pur_target_phospho/coef_results.txt'
out = fp.replace('coef_results.txt', 'driver_scores_p05.txt')

In [41]:
df = pd.read_csv(fp, sep='\t')
df

coef       p-value           FDR  -log10(FDR)  \
0       0.327489  1.879007e-46  1.192255e-45    44.923631   
1       0.070255  7.486575e-04  1.040277e-03     2.982851   
2       1.085300  1.297107e-37  6.575589e-37    36.182065   
3       0.000000           NaN           NaN          NaN   
4      -0.288698  2.163445e-20  6.477679e-20    19.188581   
...          ...           ...           ...          ...   
671395  0.000000           NaN           NaN          NaN   
671396  0.527256  3.703482e-01  9.236572e-01     0.034489   
671397  0.007996  9.886718e-01  9.993513e-01     0.000282   
671398  0.000000           NaN           NaN          NaN   
671399  0.000000           NaN           NaN          NaN   

                                   feature  driver  \
0                          driver_gene_cnv    ABL1   
1                              TumorPurity    ABL1   
2       driver_gene_has_nonsilent_mutation    ABL1   
3       driver_gene_is_pathogenic_germline    ABL1   
4                          driver_gene_cnv    ABL1   
...                                    ...     ...   
671395  driver_gene_is_pathogenic_germline  ZNF750   
671396                         TumorPurity  ZNF750   
671397                     driver_gene_cnv  ZNF750   
671398  driver_gene_has_nonsilent_mutation  ZNF750   
671399  driver_gene_is_pathogenic_germline  ZNF750   

                                                  target disease  model_r2  \
0           ABL1_S588|ABL1|NP_009297.2_S588s_1_1_588_588      BR  0.676192   
1           ABL1_S588|ABL1|NP_009297.2_S588s_1_1_588_588      BR  0.676192   
2           ABL1_S588|ABL1|NP_009297.2_S588s_1_1_588_588      BR  0.676192   
3           ABL1_S588|ABL1|NP_009297.2_S588s_1_1_588_588      BR  0.676192   
4           ABL1_T871|ABL1|NP_009297.2_T871t_1_1_871_871      BR  0.421106   
...                                                  ...     ...       ...   
671395   ZNF740_S44|ZNF740|NP_001004304.1_S44s_1_1_44_44   ccRCC -0.320278   
671396  ZNF777_S604|ZNF777|NP_056509.2_S604s_1_1_604_604   ccRCC -0.023638   
671397  ZNF777_S604|ZNF777|NP_056509.2_S604s_1_1_604_604   ccRCC -0.023638   
671398  ZNF777_S604|ZNF777|NP_056509.2_S604s_1_1_604_604   ccRCC -0.023638   
671399  ZNF777_S604|ZNF777|NP_056509.2_S604s_1_1_604_604   ccRCC -0.023638   

        model_r2_FDR  
0       3.572682e-63  
1       3.572682e-63  
2       3.572682e-63  
3       3.572682e-63  
4       6.013695e-31  
...              ...  
671395  9.668873e-01  
671396  8.924296e-01  
671397  8.924296e-01  
671398  8.924296e-01  
671399  8.924296e-01  

[671400 rows x 10 columns]

N = number of protein pairs/rows for given driver

C = coef

one version with all, and one with p < .05

In [42]:
def calculate_s2(n, cs):
    num = np.sum(np.square(cs))
    num = np.sqrt(num / n)
    return num

def calculate_s4(ps, n, s2):
    return -np.log10(np.sum(ps) / n) * s2

def calculate_s5(ps, n, s2):
    return -np.log10(n / np.sum(1 / ps)) * s2

def calculate_scores(df, driver, disease=None, feature=None, fdr=None):
    filtered = df[df['driver']==driver]
    filtered = filtered[['coef', 'p-value', 'feature', 'driver', 'target', 'disease', 'model_r2_FDR']]
    filtered = filtered[np.sum(pd.isnull(filtered.values), axis=1).flatten()==0]
    if fdr is not None:
        filtered = filtered[filtered['model_r2_FDR']<=fdr]
    if disease is not None:
        filtered = filtered[filtered['disease']==disease]
    if feature is not None:
        filtered = filtered[filtered['feature']==feature]

    n = filtered.shape[0]
    
    cs = filtered['coef'].to_numpy()
    ps = filtered['p-value'].to_numpy()
    
    s2 = calculate_s2(n, cs)
    s4 = calculate_s4(ps, n, s2)
    s5 = calculate_s5(ps, n, s2)
    
    return s2, s4, s5
    
    
    
    

In [43]:
data = []
fdr = .05
# fdr = None
drivers = sorted(set(df['driver']))
types = sorted(set(df['feature']))
for driver in drivers:
    s2, s4, s5 = calculate_scores(df, driver, fdr=fdr)
    data.append([driver, 'pancan', 'all', s2, s4, s5])
    for disease in sorted(set(df['disease'])):
        s2, s4, s5 = calculate_scores(df, driver, disease=disease, fdr=fdr)
        data.append([driver, disease, 'all', s2, s4, s5])
        for t in types:
            s2, s4, s5 = calculate_scores(df, driver, disease=disease, feature=t, fdr=fdr)
            data.append([driver, disease, t, s2, s4, s5])
results = pd.DataFrame(data=data, columns=['driver', 'disease', 'feature', 's2', 's4', 's5'])
results

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: divide by zero encountered in true_divide
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: divide by zero encountered in log10
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.p

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: divide by zero encountered in true_divide
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: divide by zero encountered in log10
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: divide by zero encountered in true_divide
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: divide by zero encountered in log10
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launc

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

...

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in double_scalars
  import sys
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:10: RuntimeWarning: invalid value encountered in double_scalars
  # Remove the CWD from sys.path while we load stuff.
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in double_scalars
  This is separate from the ipykernel package so we can avoid doing imports until
/diskmnt/Projects/Users/estorrs/miniconda3/envs/cptac_driver/lib/python3

driver disease                             feature        s2        s4  \
0       ABL1  pancan                                 all  0.685515  0.842446   
1       ABL1      BR                                 all  0.855083  1.060222   
2       ABL1      BR                         TumorPurity  0.545013  0.678332   
3       ABL1      BR                     driver_gene_cnv  0.627844  1.046203   
4       ABL1      BR  driver_gene_has_nonsilent_mutation  1.225672  1.257629   
...      ...     ...                                 ...       ...       ...   
8206  ZNF750   ccRCC                                 all       NaN       NaN   
8207  ZNF750   ccRCC                         TumorPurity       NaN       NaN   
8208  ZNF750   ccRCC                     driver_gene_cnv       NaN       NaN   
8209  ZNF750   ccRCC  driver_gene_has_nonsilent_mutation       NaN       NaN   
8210  ZNF750   ccRCC  driver_gene_is_pathogenic_germline       NaN       NaN   

              s5  
0            inf  
1     138.002608  
2      44.174516  
3     101.627878  
4     150.698004  
...          ...  
8206         NaN  
8207         NaN  
8208         NaN  
8209         NaN  
8210         NaN  

[8211 rows x 6 columns]

In [44]:
results.to_csv(out, sep='\t', index=False)

In [45]:
results

driver disease                             feature        s2        s4  \
0       ABL1  pancan                                 all  0.685515  0.842446   
1       ABL1      BR                                 all  0.855083  1.060222   
2       ABL1      BR                         TumorPurity  0.545013  0.678332   
3       ABL1      BR                     driver_gene_cnv  0.627844  1.046203   
4       ABL1      BR  driver_gene_has_nonsilent_mutation  1.225672  1.257629   
...      ...     ...                                 ...       ...       ...   
8206  ZNF750   ccRCC                                 all       NaN       NaN   
8207  ZNF750   ccRCC                         TumorPurity       NaN       NaN   
8208  ZNF750   ccRCC                     driver_gene_cnv       NaN       NaN   
8209  ZNF750   ccRCC  driver_gene_has_nonsilent_mutation       NaN       NaN   
8210  ZNF750   ccRCC  driver_gene_is_pathogenic_germline       NaN       NaN   

              s5  
0            inf  
1     138.002608  
2      44.174516  
3     101.627878  
4     150.698004  
...          ...  
8206         NaN  
8207         NaN  
8208         NaN  
8209         NaN  
8210         NaN  

[8211 rows x 6 columns]